# Neteja de dades i regressió logística

Emprarem les dades del **Fifa22**. [Enllaç](https://www.kaggle.com/datasets/bryanb/fifa-player-stats-database?resource=download&select=FIFA22_official_data.csv)

> The dataset contains +17k unique players and more than 60 columns, general information and all KPIs the famous videogame offers. As the esport scene keeps rising espacially on FIFA, I thought it can be useful for the community (kagglers and/or gamers)
>
>Context
>
>The data was retrieved thanks to a crawler that I implemented to retrieve:
>
>    Aggregated data such as name of the players, age, country
>    Detailed data such as offensive potential, defense, acceleration
>    I like football a lot and this dataset is for me the opportunity to bring my contribution for the realization of projects that can go from simple analysis to elaboration of strategies on optimal composition under constraints…


L'objectiu d'aquesta **mini** pràctica es prediure la possició del jugador emprant entre totes les característiques disponibles quatre. S'han d'entrenar dos classificadors lineals: **Regressió Logística** i **Perceptró**. 


## Importam llibraries

El que primer fem, com sempre, és importar les llibreries que emprarem. **Pot ser que per fer l'exercici necessitis importar més llibreries**.

In [14]:
from sklearn.model_selection import train_test_split
from sklearn import linear_model

import pandas as pd
import numpy as np

## Llegim les dades

Per llegir les dades emprarem la llibreria de ``pandas``. El fitxer en qüestió és el fitxer que heu descarregat de Kaggle.

In [18]:
pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',None)

In [19]:
df = pd.read_csv("./FIFA22_official_data.csv")
df.head()

ID             Name  Age  \
0  212198  Bruno Fernandes   26   
1  209658      L. Goretzka   26   
2  176580        L. Suárez   34   
3  192985     K. De Bruyne   30   
4  224334         M. Acuña   29   

                                              Photo Nationality  \
0  https://cdn.sofifa.com/players/212/198/22_60.png    Portugal   
1  https://cdn.sofifa.com/players/209/658/22_60.png     Germany   
2  https://cdn.sofifa.com/players/176/580/22_60.png     Uruguay   
3  https://cdn.sofifa.com/players/192/985/22_60.png     Belgium   
4  https://cdn.sofifa.com/players/224/334/22_60.png   Argentina   

                                  Flag  Overall  Potential  \
0  https://cdn.sofifa.com/flags/pt.png       88         89   
1  https://cdn.sofifa.com/flags/de.png       87         88   
2  https://cdn.sofifa.com/flags/uy.png       88         88   
3  https://cdn.sofifa.com/flags/be.png       91         91   
4  https://cdn.sofifa.com/flags/ar.png       84         84   

                 Club                                Club Logo    Value  \
0   Manchester United   https://cdn.sofifa.com/teams/11/30.png  €107.5M   
1   FC Bayern München   https://cdn.sofifa.com/teams/21/30.png     €93M   
2  Atlético de Madrid  https://cdn.sofifa.com/teams/240/30.png   €44.5M   
3     Manchester City   https://cdn.sofifa.com/teams/10/30.png  €125.5M   
4          Sevilla FC  https://cdn.sofifa.com/teams/481/30.png     €37M   

    Wage  Special Preferred Foot  International Reputation  Weak Foot  \
0  €250K     2341          Right                       3.0        3.0   
1  €140K     2314          Right                       4.0        4.0   
2  €135K     2307          Right                       5.0        4.0   
3  €350K     2304          Right                       4.0        5.0   
4   €45K     2292           Left                       2.0        3.0   

   Skill Moves     Work Rate         Body Type Real Face  \
0          4.0    High/ High            Unique       Yes   
1          3.0  High/ Medium            Unique       Yes   
2          3.0  High/ Medium            Unique       Yes   
3          4.0    High/ High            Unique       Yes   
4          4.0    High/ High  Stocky (170-185)        No   

                      Position  Jersey Number        Joined Loaned From  \
0  <span class="pos pos18">CAM           18.0  Jan 30, 2020         NaN   
1  <span class="pos pos11">LDM            8.0   Jul 1, 2018         NaN   
2   <span class="pos pos24">RS            9.0  Sep 25, 2020         NaN   
3  <span class="pos pos13">RCM           17.0  Aug 30, 2015         NaN   
4    <span class="pos pos7">LB           19.0  Sep 14, 2020         NaN   

  Contract Valid Until Height Weight  Crossing  Finishing  HeadingAccuracy  \
0                 2025  179cm   69kg      87.0       83.0             64.0   
1                 2026  189cm   82kg      75.0       82.0             86.0   
2                 2022  182cm   83kg      80.0       93.0             84.0   
3                 2025  181cm   70kg      94.0       82.0             55.0   
4                 2024  172cm   69kg      87.0       66.0             58.0   

   ShortPassing  Volleys  Dribbling  Curve  FKAccuracy  LongPassing  \
0          91.0     87.0       83.0   87.0        87.0         88.0   
1          86.0     69.0       84.0   76.0        75.0         84.0   
2          83.0     90.0       83.0   86.0        82.0         77.0   
3          94.0     82.0       88.0   85.0        83.0         93.0   
4          82.0     68.0       87.0   88.0        75.0         78.0   

   BallControl  Acceleration  SprintSpeed  Agility  Reactions  Balance  \
0         87.0          77.0         73.0     80.0       91.0     79.0   
1         87.0          78.0         83.0     76.0       88.0     71.0   
2         86.0          76.0         69.0     75.0       92.0     78.0   
3         91.0          76.0         76.0     79.0       91.0     78.0   
4         88.0          77.0         76.0     83.0  

In [21]:
df[df["Best Position"]=="GK"]

ID                   Name  Age  \
10736   21570        14 Rogério Ceni   40   
11192  210257                Ederson   27   
12350  167495               M. Neuer   35   
12410  163301              J. Orozco   35   
13109  204935            J. Pickford   27   
13177  226753            21 A. Onana   24   
13363  174543               C. Bravo   38   
13755  215698             M. Maignan   25   
13832  202811            E. Martínez   28   
13837  205186           P. Gazzaniga   29   
13890  192448          M. ter Stegen   29   
14022  199339             M. Riemann   32   
14087  193041               K. Navas   34   
14134  193080                 De Gea   30   
14137  224348               L. Hoyos   32   
14244  200389               J. Oblak   28   
14279  257439               R. Ofori   27   
14311  222511              E. Unsain   26   
14352  176919              N. Guzmán   35   
14455  212831                Alisson   28   
14507  182494             F. Muslera   35   
14522  200159              S. Ortega   28   
14587  220604                  Jaume   30   
14601  193105              A. Areola   28   
14608  230621          G. Donnarumma   22   
14615  199482               A. Lopes   30   
14644  167948              H. Lloris   34   
14658  189690                 Guaita   34   
14674  201095           A. Marchesín   33   
14679  178750          Sergio Asenjo   32   
14680  178005           Rui Patrício   33   
14686  135339               14 Fábio   32   
14725  215985             F. Monetti   31   
14742  163587          K. Schmeichel   34   
14753  192563                B. Leno   29   
14758  177683              Y. Sommer   32   
14770  199005                M. Ryan   29   
14795  165247               I. Khune   34   
14827  223550               J. Omlin   27   
14835  199575            Jordi Masip   32   
14838  230318          Nelsildo Reis   21   
14839    3813         14 M. Landreau   34   
14848  139968          19 V. Enyeama   34   
14856  132740              J. Hansen   36   
14857  221087              Pau López   26   
14865  205211              M. Borjan   33   
14868  198625                S. Bain   29   
14874  176526              L. Burián   37   
14877  156433            A. Talavera   38   
14894  253012             L. Morales   21   
14896  241671           D. Livaković   26   
14902  228279             J. Drommel   24   
14905  194404                   Neto   31   
14913  193314                  Aitor   30   
14926  220407            M. Dúbravka   32   
14932  156483           C. Lucchetti   43   
14937  192119            T. Courtois   29   
14947  199987           J. Cillessen   32   
14958  178086                   Adán   34   
14961  169181             K. Vermeer   35   
14964  240784              J. Bursik   20   
14967  234777             Z. Steffen   26   
14971  110082               14 Pinto   37   
14972  182224             Wang Dalei   32   
14977  203042             J. Butland   28   
14983  226300               U. Çakır   25   
14989  146296       Andrés Fernández   34   
14990   24630             Pepe Reina   38   
14991  186153            W. Szczęsny   31   
14996  215251             G. Herrera   29   
15002  204120              T. Vaclík   32   
15008  176895            21 M. Pinto   36   
15012  167958              14 Cássio   26   
15015  177644           Kiko Casilla   34   
15016  204966          Adrián Ortolá   27   
15017  228736             W. Faríñez   23   
15022  164853            A. Federici   36   
15026  192984            K. Casteels   29   
15029  215316               G. Rulli   29   
15036  194730            Juan Carlos   33   
15039  177723               Fabricio   33   
15041  224041             M. Schwäbe   26   
15042  224836    V. Milinković-Savić   24   
15044  167993           V. Stojković   37   
15048  202089               L. Mejía   30   
15050   49000            A. McGregor   39   
15054  199493           Diego Mariño   31   
15055  223249               G. Arias   33   
15056 

## EDA: *Exploratory data analysis*


In [8]:
df.describe()

ID           Age       Overall     Potential       Special  \
count   16710.000000  16710.000000  16710.000000  16710.000000  16710.000000   
mean   220560.467923     25.727409     67.646320     72.572292   1652.497307   
std     38496.607959      5.048910      6.457695      5.688085    257.271696   
min        27.000000     16.000000     28.000000     38.000000    571.000000   
25%    203891.250000     22.000000     63.000000     69.000000   1525.000000   
50%    229253.000000     25.000000     68.000000     72.000000   1687.000000   
75%    245368.750000     29.000000     72.000000     76.000000   1826.000000   
max    264704.000000     54.000000     93.000000     95.000000   2341.000000   

       International Reputation     Weak Foot   Skill Moves  Jersey Number  \
count              16710.000000  16710.000000  16710.000000   16684.000000   
mean                   1.169958      3.008199      2.475464      20.458643   
std                    0.485305      0.681742      0.791414      17.699813   
min                    1.000000      1.000000      1.000000       1.000000   
25%                    1.000000      3.000000      2.000000       8.000000   
50%                    1.000000      3.000000      2.000000      17.000000   
75%                    1.000000      3.000000      3.000000      27.000000   
max                    5.000000      5.000000      5.000000      99.000000   

           Crossing     Finishing  HeadingAccuracy  ShortPassing  \
count  16710.000000  16710.000000     16710.000000  16710.000000   
mean      52.212448     48.725075        54.123339     61.314423   
std       17.772348     19.401715        17.007831     13.665353   
min        7.000000      3.000000         5.000000      8.000000   
25%       42.000000     34.000000        46.000000     57.000000   
50%       57.000000     53.000000        57.000000     64.000000   
75%       65.000000     64.000000        66.000000     70.000000   
max       94.000000     95.000000        93.000000     94.000000   

            Volleys     Dribbling         Curve    FKAccuracy   LongPassing  \
count  16673.000000  16710.000000  16673.000000  16710.000000  16710.000000   
mean      45.652972     58.591203     50.574522     45.074087     55.454877   
std       17.828225     17.925005     18.237536     17.596471     14.494716   
min        4.000000      5.000000      6.000000      4.000000      9.000000   
25%       33.000000     54.000000     39.000000     33.000000     47.000000   
50%       48.000000     63.500000     53.000000     44.000000     58.000000   
75%       59.000000     70.000000     64.000000     59.000000     66.000000   
max       90.000000     96.000000     94.000000     94.000000     93.000000   

        BallControl  Acceleration   SprintSpeed       Agility     Reactions  \
count  16710.000000  16710.000000  16710.000000  16673.000000  16710.000000   
mean      61.387433     65.684919     65.783124     65.222875     63.592400   
std       15.673348     15.005583     14.737924     14.512499      8.594003   
min        8.000000     13.000000     15.000000     18.000000     28.000000   
25%       58.000000     58.000000     59.000000     57.000000     58.000000   
50%       65.000000     68.000000     68.000000     68.000000     64.000000   
75%       71.000000     76.000000     76.000000     75.000000     69.000000   
max       96.000000     97.000000     97.000000     96.000000     96.000000   

            Balance     ShotPower       Jumping       Stamina      Strength  \
count  16673.000000  16710.000000  16673.000000  16710.000000  16710.000000   
mean      64.943262     60.642190     65.896659     64.204548     66.266008   
std       14.257323     12.959795     12.285499     15.575110     12.624115   
min       19.000000     12.000000     22.000000     13.000000     18.000000   
25%       57.000000     52.000000     59.000000     57.000000     59.000000   
50%       67.000000     62.000000     67.000000     67.000000     68.000000   
75% 

## Entrenament

In [10]:
df.corr()

ID       Age   Overall  Potential   Special  \
ID                        1.000000 -0.778619 -0.380127   0.146391 -0.194943   
Age                      -0.778619  1.000000  0.473963  -0.291925  0.251852   
Overall                  -0.380127  0.473963  1.000000   0.586648  0.576851   
Potential                 0.146391 -0.291925  0.586648   1.000000  0.290843   
Special                  -0.194943  0.251852  0.576851   0.290843  1.000000   
International Reputation -0.476212  0.359957  0.511914   0.335564  0.278249   
Weak Foot                -0.082038  0.076093  0.190012   0.124341  0.315141   
Skill Moves              -0.053215  0.058754  0.319352   0.207014  0.708170   
Jersey Number             0.161056 -0.215230 -0.198334   0.023400 -0.119632   
Crossing                 -0.130067  0.135549  0.357150   0.173882  0.854284   
Finishing                -0.083087  0.085817  0.287630   0.160098  0.719047   
HeadingAccuracy          -0.134388  0.171271  0.301434   0.122842  0.613581   
ShortPassing             -0.139180  0.150744  0.483895   0.308806  0.900542   
Volleys                  -0.182732  0.175433  0.338185   0.149438  0.755599   
Dribbling                -0.020554  0.008679  0.328883   0.248354  0.864322   
Curve                    -0.171575  0.166627  0.369446   0.179994  0.845994   
FKAccuracy               -0.212644  0.213594  0.338062   0.129219  0.781589   
LongPassing              -0.187007  0.204621  0.474325   0.269037  0.841629   
BallControl              -0.094847  0.088814  0.413273   0.278631  0.896694   
Acceleration              0.221726 -0.237159  0.117279   0.195941  0.581925   
SprintSpeed               0.225480 -0.230065  0.126716   0.193727  0.563291   
Agility                   0.061317 -0.073190  0.190397   0.159914  0.657450   
Reactions                -0.384946  0.472808  0.869650   0.461446  0.584355   
Balance                   0.058997 -0.101258  0.085925   0.116756  0.583423   
ShotPower                -0.244912  0.294943  0.513840   0.231442  0.692078   
Jumping                  -0.143951  0.205118  0.242756   0.035364  0.281309   
Stamina                   0.049421  0.042786  0.315613   0.147060  0.755738   
Strength                 -0.239924  0.348877  0.321999  -0.001678  0.175991   
LongShots                -0.159989  0.172365  0.361913   0.160376  0.826613   
Aggression               -0.205479  0.268597  0.363796   0.107848  0.654495   
Interceptions            -0.142384  0.182175  0.292148   0.119569  0.541181   
Positioning              -0.096612  0.100933  0.317741   0.170101  0.819526   
Vision                   -0.214288  0.221505  0.495250   0.282933  0.767604   
Penalties                -0.197570  0.193408  0.301394   0.124394  0.713650   
Composure                -0.380347  0.405267  0.683421   0.322608  0.786444   
Marking                  -0.046743  0.128716  0.159226   0.082908  0.411837   
StandingTackle           -0.060386  0.096033  0.231631   0.123196  0.528911   
SlidingTackle            -0.048152  0.080387  0.205826   0.113628  0.492826   
GKDiving                 -0.087949  0.115862  0.025537  -0.011004 -0.656966   
GKHandling               -0.099387  0.121970  0.027278  -0.010710 -0.656078   
GKKicking                -0.119287  0.126655  0.030399  -0.005323 -0.650283   
GKPositioning            -0.102843  0.127909  0.032042  -0.009069 -0.653125   
GKReflexes               -0.093801  0.118076  0.028252  -0.009003 -0.657127   
Best Overall Rating      -0.319224  0.399066  0.985377   0.633093  0.603120   
DefensiveAwareness       -0.130528  0.158146  0.284514   0.119204  0.557387   

                          International Reputation  Weak Foot  Skill Moves  \
ID                                       -0.476212  -0.082038    -0.053215   
Age                                       0.359957   0.076093     0.058754   
Overall                                   0.511914   0.190012     0.319352   
Potential                                 0.335564   0.124341     0.207014   
Special

## Avaluació